In [42]:
"""
This file contains code to

    (a) Load the pre-trained classifier and
    associated files.

    (b) Transform new input data into the
    correct format for the classifier.

    (c) Run the classifier on the transformed
    data and return results.
"""

import pickle
import numpy as np
import pandas as pd
from sklearn.externals import joblib
from sklearn.svm import LinearSVC
from sklearn.linear_model import LogisticRegression
from sklearn.feature_selection import SelectFromModel
from sklearn.feature_extraction.text import TfidfVectorizer
import nltk
nltk.download('stopwords')
nltk.download('vader_lexicon')
from nltk.stem.porter import *
import string
import re

from nltk.sentiment.vader import SentimentIntensityAnalyzer as VS
from textstat import *


stopwords=stopwords = nltk.corpus.stopwords.words("english")

other_exclusions = ["#ff", "ff", "rt"]
stopwords.extend(other_exclusions)

sentiment_analyzer = VS()

stemmer = PorterStemmer()


def preprocess(text_string):
    """
    Accepts a text string and replaces:
    1) urls with URLHERE
    2) lots of whitespace with one instance
    3) mentions with MENTIONHERE

    This allows us to get standardized counts of urls and mentions
    Without caring about specific people mentioned
    """
    space_pattern = '\s+'
    giant_url_regex = ('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|'
        '[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')
    mention_regex = '@[\w\-]+'
    parsed_text = re.sub(space_pattern, ' ', text_string)
    parsed_text = re.sub(giant_url_regex, 'URLHERE', parsed_text)
    parsed_text = re.sub(mention_regex, 'MENTIONHERE', parsed_text)
    #parsed_text = parsed_text.code("utf-8", errors='ignore')
    return parsed_text

def tokenize(tweet):
    """Removes punctuation & excess whitespace, sets to lowercase,
    and stems tweets. Returns a list of stemmed tokens."""
    tweet = " ".join(re.split("[^a-zA-Z]*", tweet.lower())).strip()
    #tokens = re.split("[^a-zA-Z]*", tweet.lower())
    tokens = [stemmer.stem(t) for t in tweet.split()]
    return tokens

def basic_tokenize(tweet):
    """Same as tokenize but without the stemming"""
    tweet = " ".join(re.split("[^a-zA-Z.,!?]*", tweet.lower())).strip()
    return tweet.split()

def get_pos_tags(tweets):
    """Takes a list of strings (tweets) and
    returns a list of strings of (POS tags).
    """
    tweet_tags = []
    for t in tweets:
        tokens = basic_tokenize(preprocess(t))
        tags = nltk.pos_tag(tokens)
        tag_list = [x[1] for x in tags]
        #for i in range(0, len(tokens)):
        tag_str = " ".join(tag_list)
        tweet_tags.append(tag_str)
    return tweet_tags

def count_twitter_objs(text_string):
    """
    Accepts a text string and replaces:
    1) urls with URLHERE
    2) lots of whitespace with one instance
    3) mentions with MENTIONHERE
    4) hashtags with HASHTAGHERE

    This allows us to get standardized counts of urls and mentions
    Without caring about specific people mentioned.

    Returns counts of urls, mentions, and hashtags.
    """
    space_pattern = '\s+'
    giant_url_regex = ('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|'
        '[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')
    mention_regex = '@[\w\-]+'
    hashtag_regex = '#[\w\-]+'
    parsed_text = re.sub(space_pattern, ' ', text_string)
    parsed_text = re.sub(giant_url_regex, 'URLHERE', parsed_text)
    parsed_text = re.sub(mention_regex, 'MENTIONHERE', parsed_text)
    parsed_text = re.sub(hashtag_regex, 'HASHTAGHERE', parsed_text)
    return(parsed_text.count('URLHERE'),parsed_text.count('MENTIONHERE'),parsed_text.count('HASHTAGHERE'))

def other_features_(tweet):
    """This function takes a string and returns a list of features.
    These include Sentiment scores, Text and Readability scores,
    as well as Twitter specific features.

    This is modified to only include those features in the final
    model."""

    sentiment = sentiment_analyzer.polarity_scores(tweet)

    words = preprocess(tweet) #Get text only

    syllables = 0 #count syllables in words
    num_chars = sum(len(w) for w in words) #num chars in words
    num_chars_total = len(tweet)
    num_terms = len(tweet.split())
    num_words = len(words.split())
    avg_syl = round(float((syllables+0.001))/float(num_words+0.001),4)
    num_unique_terms = len(set(words.split()))

    ###Modified FK grade, where avg words per sentence is just num words/1
    FKRA = round(float(0.39 * float(num_words)/1.0) + float(11.8 * avg_syl) - 15.59,1)
    ##Modified FRE score, where sentence fixed to 1
    FRE = round(206.835 - 1.015*(float(num_words)/1.0) - (84.6*float(avg_syl)),2)

    twitter_objs = count_twitter_objs(tweet) #Count #, @, and http://
    features = [FKRA, FRE, syllables, num_chars, num_chars_total, num_terms, num_words,
                num_unique_terms, sentiment['compound'],
                twitter_objs[2], twitter_objs[1],]
    #features = pandas.DataFrame(features)
    return features

def get_oth_features(tweets):
    """Takes a list of tweets, generates features for
    each tweet, and returns a numpy array of tweet x features"""
    feats=[]
    for t in tweets:
        feats.append(other_features_(t))
    return np.array(feats)


def transform_inputs(tweets, tf_vectorizer, idf_vector, pos_vectorizer):
    """
    This function takes a list of tweets, along with used to
    transform the tweets into the format accepted by the model.

    Each tweet is decomposed into
    (a) An array of TF-IDF scores for a set of n-grams in the tweet.
    (b) An array of POS tag sequences in the tweet.
    (c) An array of features including sentiment, vocab, and readability.

    Returns a pandas dataframe where each row is the set of features
    for a tweet. The features are a subset selected using a Logistic
    Regression with L1-regularization on the training data.

    """
    tf_array = tf_vectorizer.fit_transform(tweets).toarray()
    tfidf_array = tf_array*idf_vector
    print "Built TF-IDF array"

    pos_tags = get_pos_tags(tweets)
    pos_array = pos_vectorizer.fit_transform(pos_tags).toarray()
    print "Built POS array"

    oth_array = get_oth_features(tweets)
    print "Built other feature array"

    M = np.concatenate([tfidf_array, pos_array, oth_array],axis=1)
    return pd.DataFrame(M)

def predictions(X, model):
    """
    This function calls the predict function on
    the trained model to generated a predicted y
    value for each observation.
    """
    y_preds = model.predict(X)
    return y_preds

def class_to_name(class_label):
    """
    This function can be used to map a numeric
    feature name to a particular class.
    """
    if class_label == 0:
        return "Hate speech"
    elif class_label == 1:
        return "Offensive language"
    elif class_label == 2:
        return "Neither"
    else:
        return "No label"

def get_tweets_predictions(tweets, perform_prints=True):
    fixed_tweets = []
    for i, t_orig in enumerate(tweets):
        s = t_orig
        try:
            s = s.encode("latin1")
        except:
            try:
                s = s.encode("utf-8")
            except:
                pass
        if type(s) != unicode:
            fixed_tweets.append(unicode(s, errors="ignore"))
        else:
            fixed_tweets.append(s)
    assert len(tweets) == len(fixed_tweets), "shouldn't remove any tweets"
    tweets = fixed_tweets
    print len(tweets), " tweets to classify"

    print "Loading trained classifier... "
    model = joblib.load('final_model.pkl')

    print "Loading other information..."
    tf_vectorizer = joblib.load('final_tfidf.pkl')
    idf_vector = joblib.load('final_idf.pkl')
    pos_vectorizer = joblib.load('final_pos.pkl')
    #Load ngram dict
    #Load pos dictionary
    #Load function to transform data

    print "Transforming inputs..."
    X = transform_inputs(tweets, tf_vectorizer, idf_vector, pos_vectorizer)

    print "Running classification model..."
    predicted_class = predictions(X, model)

    return predicted_class


if __name__ == '__main__':
    print "Loading data to classify..."

    #Tweets obtained here: https://github.com/sashaperigo/Trump-Tweets

    df = pd.read_csv('trump_tweets.csv')
    trump_tweets = df.Text
    trump_tweets = [x for x in trump_tweets if type(x) == str]
    trump_predictions = get_tweets_predictions(trump_tweets)

    print "Printing predicted values: "
    for i,t in enumerate(trump_tweets):
        print t
        print class_to_name(trump_predictions[i])
        print 

    print "Calculate accuracy on labeled data"
    df = pd.read_csv('labeled_data.csv')
    tweets = df['tweet'].values
    tweets = [x for x in tweets if type(x) == str]
    tweets_class = df['class'].values
    predictions = get_tweets_predictions(tweets)
    right_count = 0
    for i,t in enumerate(tweets):
        if tweets_class[i] == predictions[i]:
            right_count += 1

    accuracy = right_count / float(len(df))
    print "accuracy", accuracy

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ashle\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package vader_lexicon to
[nltk_data]     C:\Users\ashle\AppData\Roaming\nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!
Loading data to classify...
29885  tweets to classify
Loading trained classifier... 
Loading other information...
Transforming inputs...
Built TF-IDF array
Built POS array
Built other feature array
Running classification model...
Printing predicted values: 
Nielson Media Research final numbers on ACCEPTANCE SPEECH: TRUMP  32.2 MILLION.  CLINTON 27.8 MILLION.  Thank you!
Neither

Thank you to all of the television viewers that made my speech at the Republican National Convention #1 over Crooked Hillary and DEMS.
Neither

Can you imagine if I had the small crowds that Hillary is drawing today in Pennsylvania. It would be a major media event! @CNN @FoxNews
Neither

N

Neither

Hillary Clinton surged the trade deficit with China 40% as
Secretary of State, costing Americans millions of jobs.
Neither

Hillary says this election is about judgment.  She's right.  Her judgement has killed thousands, unleashed ISIS and wrecked the economy.
Neither

I will be making a big speech tomorrow to discuss the failed policies and bad judgment of Crooked Hillary Clinton.
Neither

Crooked Hillary Clinton is totally unfit to be our president-really bad judgement and a temperament, according to new book, which is a mess!
Neither

When I said that if, within the Orlando club, you had some people with guns, I was obviously talking about additional guards or employees
Neither

.@DJohnsonPGA We are so proud of you Dustin. Your reaction under pressure was amazing. First of many Majors. You are a true CHAMPION!
Neither

"@bfraser747: Watch out HillaryClinton  Support @realDonaldTrump   #MakeAmericaGreatAgain  pic.twitter.com/UTYOLo7wGF"
Neither

Yesterday's failing @NYTimes 


On the way to the great state of Rhode Island- big rally. Then to Pennsylvania for rest of day and night!
Neither

Kasich just announced that he wants the people of Indiana to vote for him. Typical politician - can't make a deal work.
Neither

Shows how weak and desperate Lyin' Ted is when he has to team up with a guy who openly can't stand him and is only 1 win and 38 losses.
Neither

Lyin' Ted Cruz and 1 for 38 Kasich are unable to beat me on their own so they have to team up (collusion) in a two on one. Shows weakness!
Neither

Lyin' Ted and Kasich are mathematically dead and totally desperate. Their donors & special interest groups are not happy with them. Sad!
Neither

Wow, just announced that Lyin' Ted and Kasich are going to collude in order to keep me from getting the Republican nomination. DESPERATION!
Neither

I am happy to hear how badly the @nytimes is doing. It is a seriously failing paper with readership which is way down. Becoming irrelevant!
Neither

"@DiamondandSilk: 

.@pastormarkburns You were great last night and we all very much appreciate it! Thank you!
Neither

I will be interviewed on @foxandfriends at 8:30 A.M. ENJOY!
Neither

Will be interviewed on @Morning_Joe at 7:40. ENJOY!
Neither

Will be interviewed on @NewDay on @CNN at 7:15 A.M.
Neither

Will be interviewed on @GMA at 7:00 A.M. Big wins last night!
Neither

"@lucyric13835428: @realDonaldTrump @megynkelly  That's funny, I switched to other media too, can't stand her"
Neither

"@MaryEH428: @RealBenCarson I thank God you are on board with @realDonaldTrump to help him and us #MakeAmericaGreatAgain Ty!!"
Neither

Thank you Marco, I agree!pic.twitter.com/PTfFzFno9p
Neither

I only wish my wonderful daughter Tiffany could have been with us at 
Mar-a-Lago for our great election victory. She is a winner!
Neither

Thank you Illinois! #SuperTuesday
#MakeAmericaGreatAgain #Trump2016pic.twitter.com/vcfstc6Wnb
Neither

Thank you, North Carolina! #Trump2016 #SuperTuesday�� 
#MakeAmericaGreatAgainpi

Jeb Bush is desperate - strongly in favor of #CommonCore and very weak on illegal immigration.
Neither

Thank you for your support at this mornings Town Hall- in Salem, New Hampshire. #FITN #NHPrimarypic.twitter.com/4m6dabtxCV
Neither

Jeb Bush has zero communication skills so he spent a fortune of special interest money on a Super Bowl ad. He is a weak candidate!
Neither

My two wonderful sons, Don and Eric, will be on @foxandfriends at 7:02 - now! Enjoy.
Neither

So far the Super Bowl is very boring - not nearly as exciting as politics - MAKE AMERICA GREAT AGAIN!
Neither

I am in New Hampshire having a great time! Loved the #GOPDebate last night! Everybody enjoy the Super Bowl. #SuperBowlSunday #SB50
Neither

Thank you- Plymouth, New Hampshire! #FITN #NHPrimarypic.twitter.com/1hzn6iZIEw
Neither

Thank you Newt!https://twitter.com/newtgingrich/status/696369599818772480�ʉ�_
Neither

We are going to have a big event at the Verizon Wireless Arena in Manchester, New Hampshire! 5K+! Join u

...

Neither

Sure--@BarackObama's literary agent claims the 1991 booklet was a 'mistake' http://abcn.ws/KyYWNA�� Pretty convenient.
Neither

Let's take a closer look at that birth certificate. @BarackObama was described in 2003 as being "born in Kenya." http://bit.ly/Klc9Uu��
Neither

Reckless! Why is @BarackObama wasting over $70 Billion on 'climate change activities?' Will he ever learn? 
http://thedc.com/JnQpHU��
Neither

The @ArsenioOfficial & @ClayAiken #CelebrityApprentice live finale is going to shock you! MUST SEE TV...9 pm Sunday on NBC
Neither

The final two- @ClayAiken & @ArsenioOfficial- in the lobby of Trump Tower- http://on.fb.me/L5fvfL�� #CelebrityApprentice
Neither

Sacha Baron Cohen's new movie "The Dictator" is a complete dud. Lots of bad reviews. Besides, he should (cont) http://tl.gd/hffsu7��
Neither

Eddie Malloy, Construction Union Leader, tough as hell but fair, an amazing guy. Went to his funeral this (cont) http://tl.gd/hffmh7��
Neither

John Travolta got lucky. Th

Now Michelle Obama plays class warfare while fundraising http://bit.ly/zVyW1S��  Why is anyone donating to a (cont) http://tl.gd/g5c25q��
Neither

"Trump Tuesday" = I'll be on @SquawkBox every Tuesday morning at 7:30 a.m., on CNBC. Tune in.
Neither

The UK has run out of money and can't afford to borrow. http://tgr.ph/w63rW4�� Neither can we but that doesn't stop @BarackObama.
Neither

It is time Republicans stop attacking each other and focus on @BarackObama. America cannot survive a second term.
Neither

#trumpvlog #Oscars Oscars' Biggest Losers- Sacha Baron Cohen and Vanity Fair......http://youtu.be/v6uLhYH2EkA��
Neither

Great--with rising oil prices that are slowing economic growth, @BarackObama looks to Saudi Arabia 'to contain' (cont) http://tl.gd/g5blls��
Neither

It is time to get out of Afghanistan. We are building roads and schools for people that hate us. It is not in our national interests.
Neither

Mitt Romney says anyone who thinks there's something wrong with being succ

@BarackObama, the habitual vacationer, should read #TimeToGetTough during his upcoming 17 day Hawaii vacation.
Neither

My @hannityshow interview from Monday discussing #TimeToGetTough and the 2012 election.http://bit.ly/rT08T2��
Neither

I'll be signing copies of my new book  "Time To Get Tough" this Friday  Dec 9 in Trump Tower  from 11 a.m. t��_ (cont) http://deck.ly/~abYOp��
Neither

Whether we like it or not, oil is the axis on which the world's economies spin. It just is. When the price o��_ (cont) http://deck.ly/~qLPsC��
Neither

Get it straight: Pakistan is not our friend. When our tremendous Navy SEALS took out Osama bin Laden, they did��_ (cont) http://deck.ly/~pOSbX��
Neither

Canada's legal immigration plan starts with a simple and smart question: How will any immigrant applying fo��_ (cont) http://deck.ly/~uRmzC��
Neither

President Reagan put it best: "Welfare's purpose should be to eliminate, as far as possible, the need for its own existence."
Neither

Call me old schoo


Check out my interview on @GMA http://abcn.ws/ib1t1c
Neither

Catch me on Fox News right now, my interview with Neil Cavuto http://bit.ly/fRKfrz
Neither

@shouldtrumprun Hundreds of thousands of supporters have already gone to and joined the movement at shouldtrumprun.com  
Have you?
Neither

Some of your most popular questions answered in today's video http://bit.ly/gv6TVh
Neither

Keep talking about me: use #TrumpRoast to tweet about how good I look on @ComedyCentral tonight at 10:30/9:30c  http://bit.ly/hN3jow
Neither

Check out the Trump Fabulous World of Golf site to meet the Fazio family---master golf course designers....http://bit.ly/gi3q3E
Neither

Hey @realjeffreyross @whitney cummings @lisalampanelli: you call yourselves comedians? #TrumpRoast tonight 10:30/9:30c on @ComedyCentral.
Neither

Hey @SnoopDogg @ItstheSituation @SethMacFarlane: Oh, I'm real scared. #TrumpRoast airs tonight at 10:30/9:30 on @Comedy Central.
Neither

Watch as I humiliate a dais full of "talent."  #T

24783  tweets to classify
Loading trained classifier... 
Loading other information...
Transforming inputs...
Built TF-IDF array
Built POS array
Built other feature array
Running classification model...
accuracy 0.909696162692
